In [6]:
from math_utils import *
from plot_utils import *
from low_rank_approximation import *
import itertools

test_dir = './data/second_test'
df_path = './data/second_test.csv'
counter = itertools.count(start=1)

In [7]:
title = 'Convergence Test'
x = 'm*n'
y = 'run'
remove_outliers = 0
logscale = (True, False)
font_size = 15
fig_size = (1100, 500)

def type_fun(x):
    ret = x.split('_')[0]
    if ret == 'p':
        return 'pokemon'
    elif ret == 'h':
        return 'horse'
    elif ret == 'n':
        return 'normal'
    else:
        return 'mnist' 
def run_fun(x):
    if x == 's_img':
        return 'A'
    else:
        return 'B'
    
filter = {'c_name': lambda x: (x == 'g_img') | (x == 's_img'),
          'type': lambda x: (x == 'horse')}
new_col = {'type': lambda x: x['m_name'].apply(lambda x: type_fun(x)),
           'run': lambda x: x['c_name'].apply(lambda x: run_fun(x)),
           'error_ratio': lambda x: x['error_ratio'].apply(lambda val: 1e-16 if val < 0 else val)}

remove_col = ['pc_name', 'c_name', 'date']

fig = plot_agg_global_df(x=x, y=y, remove_outliers=remove_outliers, dataframe_path=df_path,
                         filter=filter, new_col=new_col, remove_col=remove_col,
                         logscale=logscale, title=title, font_size = font_size, fig_size = fig_size
                   )
fig.write_html('./data/plots/' + title.replace(' ', '_').lower() + '_' + str(next(counter)) + '.html')
fig.show()

m_name has too many categories
t_name has only one value:  1
init_method has only one value:  sketching_g
epsilon has only one value: 1e-08
k has only one value: 18.142857142857142
type has only one value:  horse


In [3]:
global_df = load_global_df(filter=filter, new_col=new_col, dataframe_path=df_path)

def my_function(group):
    # Carica le matrici
    m1 = load_matrices('g_img', group['m_name'].iloc[0], group['t_name'].iloc[0], test_dir=test_dir)
    m2 = load_matrices('s_img', group['m_name'].iloc[0], group['t_name'].iloc[0], test_dir=test_dir)

    # Calcola la diff_score
    diff_score = (
        np.linalg.norm(m1['V'] - m2['V'], 'fro') / max(np.linalg.norm(m2['V'], 'fro'), np.linalg.norm(m1['V'], 'fro')) +
        np.linalg.norm(m1['U'] - m2['U'], 'fro') / max(np.linalg.norm(m2['U'], 'fro'), np.linalg.norm(m1['U'], 'fro'))
    )

    # Calcola la differenza assoluta di obj_fun_abs
    diff_obj_score = abs(group['obj_fun_rel'].iloc[0] - group['obj_fun_rel'].iloc[1])

    # Crea un nuovo DataFrame per il risultato
    result = pd.DataFrame({
        'm_name': [group['m_name'].iloc[0]],
        't_name': [group['t_name'].iloc[0]],
        'diff_score': [diff_score],
        'diff_obj_score': [diff_obj_score]
    })
    return result

# Applica il GroupBy e ottieni il nuovo DataFrame
result_df = global_df.groupby(['m_name', 't_name']).apply(my_function).reset_index(drop=True)
result_df['diff_obj_score'] = result_df['diff_obj_score'] + 1e-16


C:\Users\cicci\AppData\Local\Temp\ipykernel_9784\2163077394.py:27: DeprecationWarning:

DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.



In [8]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Crea il layout con due subplot orizzontali
fig = make_subplots(
    rows=2, cols=1,  # Due righe, una colonna
    shared_xaxes=False,  # Le scale X non sono condivise
    vertical_spacing=0.1  # Distanza tra i subplot
)

# Aggiungi il boxplot per 'diff_score' nel primo subplot
fig.add_trace(
    go.Box(
        x=result_df['diff_score'],
        name='Difference Score - Solution ',
        boxmean='sd'  # Mostra la media e la deviazione standard
    ),
    row=1, col=1  # Primo subplot
)

# Aggiungi il boxplot per 'diff_obj_score' nel secondo subplot
fig.add_trace(
    go.Box(
        x=result_df['diff_obj_score'],
        name='Difference Score - Objective Function',
        boxmean='sd',  # Mostra la media e la deviazione standard
        #xaxis_title='value'
    ),
    row=2, col=1  # Secondo subplot
)

# Aggiungi titolo globale e etichette
fig.update_layout(
    title_text='Convergence Test - Difference Scores (different execution on the same matrix)',
    showlegend=False,  # Nascondi la legenda
    xaxis=dict(type='log'),  # Imposta l'asse X del primo subplot come logaritmico
    xaxis2=dict(type='log'),  # Imposta l'asse X del secondo subplot come logaritmico
    font=dict(size=15)
)

# Mostra il grafico
fig.write_html('./data/plots/' + title.replace(' ', '_').lower() + '_' + str(next(counter)) + '.html')
fig.show()


In [9]:
x = 'm*n'
y = 'error_ratio'
remove_outliers = 0
logscale = (True, True)
font_size = 15

fig = plot_agg_global_df(x=x, y=y, remove_outliers=remove_outliers, dataframe_path=df_path,
                         filter=filter, new_col=new_col, remove_col= remove_col,
                         logscale=logscale, title=title, font_size = font_size
                   )
fig.write_html('./data/plots/' + title.replace(' ', '_').lower() + '_' + str(next(counter)) + '.html')
fig.show()

m_name has too many categories
init_method has only one value:  sketching_g
epsilon has only one value: 1e-08
type has only one value:  horse
